In [ ]:
import pandas as pd

df = pd.read_parquet('/content/articles_with_text_only.parquet')
df.head()

SOURCEURL     SQLDATE  \
0  https://www.aa.com.tr/en/americas/1-dead-after...  20250101.0   
1  https://townhall.com/tipsheet/mattvespa/2025/0...  20250101.0   
2  https://www.newsweek.com/puerto-rico-power-out...  20250101.0   
3  https://saharareporters.com/2025/01/01/tesla-c...  20250101.0   
4  https://techstory.in/tamil-nadu-cancels-global...  20250101.0   

                domain                                              title  \
0            aa.com.tr  1 dead after Tesla Cybertruck explodes outside...   
1         townhall.com  Here's the Interesting Twist Regarding the Tes...   
2         newsweek.com  Puerto Rico Blackout Update as People Remain W...   
3  saharareporters.com  Tesla Cybertruck Explodes Outside Trump Hotel ...   
4         techstory.in  Tamil Nadu Cancels Global Smart Meter Tender O...   

                       entity    label  count entity_original  \
0  the Cybertruck Owners Club  PRODUCT      9      Cybertruck   
1  the Cybertruck Owners Club  PRODUCT     10      Cybertruck   
2                 Lumo Energy      ORG      9     LUMA Energy   
3                   Las Vegas      GPE      7       Las Vegas   
4                    TANGEDCO      ORG      8        TANGEDCO   

                                           TEXT_FILE  \
0  008517_www_aa_com_tr_en_americas_1-dead-after-...   
1  007860_townhall_com_tipsheet_mattvespa_2025_01...   
2  019600_www_newsweek_com_puerto-rico-power-outa...   
3  006681_saharareporters_com_2025_01_01_tesla-cy...   
4  007050_techstory_in_tamil-nadu-cancels-global-...   

                                                text  
0  https://www.aa.com.tr/en/americas/1-dead-after...  
1  https://townhall.com/tipsheet/mattvespa/2025/0...  
2  https://www.newsweek.com/puerto-rico-power-out...  
3  https://saharareporters.com/2025/01/01/tesla-c...  
4  https://techstory.in/tamil-nadu-cancels-global...

In [ ]:
df['SQLDATE'].dtype

dtype('float64')

In [ ]:
df['SQLDATE'] = df['SQLDATE'].astype('int').astype('str')
df['SQLDATE'] = pd.to_datetime(df['SQLDATE'], format='%Y%m%d')

In [ ]:
df.head()

SOURCEURL    SQLDATE  \
0  https://www.aa.com.tr/en/americas/1-dead-after... 2025-01-01   
1  https://townhall.com/tipsheet/mattvespa/2025/0... 2025-01-01   
2  https://www.newsweek.com/puerto-rico-power-out... 2025-01-01   
3  https://saharareporters.com/2025/01/01/tesla-c... 2025-01-01   
4  https://techstory.in/tamil-nadu-cancels-global... 2025-01-01   

                domain                                              title  \
0            aa.com.tr  1 dead after Tesla Cybertruck explodes outside...   
1         townhall.com  Here's the Interesting Twist Regarding the Tes...   
2         newsweek.com  Puerto Rico Blackout Update as People Remain W...   
3  saharareporters.com  Tesla Cybertruck Explodes Outside Trump Hotel ...   
4         techstory.in  Tamil Nadu Cancels Global Smart Meter Tender O...   

                       entity    label  count entity_original  \
0  the Cybertruck Owners Club  PRODUCT      9      Cybertruck   
1  the Cybertruck Owners Club  PRODUCT     10      Cybertruck   
2                 Lumo Energy      ORG      9     LUMA Energy   
3                   Las Vegas      GPE      7       Las Vegas   
4                    TANGEDCO      ORG      8        TANGEDCO   

                                           TEXT_FILE  \
0  008517_www_aa_com_tr_en_americas_1-dead-after-...   
1  007860_townhall_com_tipsheet_mattvespa_2025_01...   
2  019600_www_newsweek_com_puerto-rico-power-outa...   
3  006681_saharareporters_com_2025_01_01_tesla-cy...   
4  007050_techstory_in_tamil-nadu-cancels-global-...   

                                                text  
0  https://www.aa.com.tr/en/americas/1-dead-after...  
1  https://townhall.com/tipsheet/mattvespa/2025/0...  
2  https://www.newsweek.com/puerto-rico-power-out...  
3  https://saharareporters.com/2025/01/01/tesla-c...  
4  https://techstory.in/tamil-nadu-cancels-global...

In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
from pathlib import Path

base_dir = Path('/content/drive/MyDrive/NLPproject/texts')

In [ ]:
!cp -r "/content/drive/MyDrive/NLPproject/texts" "/content/texts_local"


In [ ]:
from pathlib import Path
base_dir = Path('/content/texts_local')   # now using local copy (faster)


In [ ]:
from pathlib import Path
import re

all_files = list(base_dir.glob('*'))
text_by_key = {}

for path in all_files:
    try:
        content = path.read_text(encoding='utf-8', errors='ignore')
    except Exception as e:
        print(f"Error reading {path}: {e}")
        continue

    # Count occurrences of "tesla" in any capitalization
    count_tesla = len(re.findall(r'tesla', content, flags=re.IGNORECASE))

    # Keep only texts where "tesla" appears at least 3 times
    if count_tesla < 3:
        continue

    # key as full filename
    text_by_key[path.name] = content
    # key as stem (filename without extension)
    text_by_key[path.stem] = content


Error reading /content/texts_local/texts: [Errno 21] Is a directory: '/content/texts_local/texts'


In [ ]:
df['article_text'] = df['TEXT_FILE'].map(text_by_key)

# Check how many are missing
missing = df['article_text'].isna().sum()
print("Rows with missing article_text:", missing)

df[['TEXT_FILE', 'article_text']].head()


Rows with missing article_text: 30842


TEXT_FILE  \
0  008517_www_aa_com_tr_en_americas_1-dead-after-...   
1  007860_townhall_com_tipsheet_mattvespa_2025_01...   
2  019600_www_newsweek_com_puerto-rico-power-outa...   
3  006681_saharareporters_com_2025_01_01_tesla-cy...   
4  007050_techstory_in_tamil-nadu-cancels-global-...   

                                        article_text  
0  https://www.aa.com.tr/en/americas/1-dead-after...  
1  https://townhall.com/tipsheet/mattvespa/2025/0...  
2                                                NaN  
3  https://saharareporters.com/2025/01/01/tesla-c...  
4                                                NaN

In [ ]:
# Group by date and concatenate all article_texts for that day
mega_df = (
    df.groupby('SQLDATE')['article_text']
      .apply(lambda texts: '\n\n'.join(t for t in texts if isinstance(t, str)))
      .reset_index(name='mega_article')
)

mega_df.head()


SQLDATE                                       mega_article
0 2025-01-01  https://www.aa.com.tr/en/americas/1-dead-after...
1 2025-01-02  https://www.newsweek.com/cybertruck-explosion-...
2 2025-01-03  https://www.irishtimes.com/world/us/2025/01/03...
3 2025-01-04  https://hotaugusta.com/2025/01/02/new-details-...
4 2025-01-05  https://www.agrinews-pubs.com:443/news/farm-eq...

In [ ]:
import re
import string
import nltk

nltk.download('punkt')
nltk.download('stopwords')
from nltk.corpus import stopwords

stop_words = set(stopwords.words('english'))

def clean_text(text):
    if not isinstance(text, str):
        return ""

    # 1. lowercase
    text = text.lower()

    # 2. remove urls
    text = re.sub(r'http\S+|www\.\S+', '', text)

    # 3. remove punctuation
    text = text.translate(str.maketrans('', '', string.punctuation))

    # 4. remove numbers
    text = re.sub(r'\d+', '', text)

    # 5. remove extra spaces
    text = re.sub(r'\s+', ' ', text).strip()

    # 6. remove stopwords
    tokens = text.split()
    tokens = [t for t in tokens if t not in stop_words]

    # 7. rejoin
    return " ".join(tokens)

# εφαρμόζουμε cleaning στο mega_article
mega_df['mega_article'] = mega_df['mega_article'].apply(clean_text)

mega_df.head()


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


SQLDATE                                       mega_article
0 2025-01-01  dead tesla cybertruck explodes outside trump h...
1 2025-01-02  cybertruck explosion suspect matthew livelsber...
2 2025-01-03  las vegas soldier’s bomb tesla outside trump h...
3 2025-01-04  lvpd identify driver cybertruck explosion hot ...
4 2025-01-05  tesla sales dropped first annual decline dozen...

In [ ]:
# 1. Drop rows where mega_article is NaN
mega_df = mega_df.dropna(subset=['mega_article'])

# 2. Convert to string
mega_df['mega_article'] = mega_df['mega_article'].astype(str)

# 3. Drop rows where mega_article is empty or whitespace
mega_df = mega_df[mega_df['mega_article'].str.strip() != ""]

# Προαιρετικά: δες πόσες γραμμές απέμειναν
print("Remaining rows after dropping:", len(mega_df))
mega_df.head()

Remaining rows after dropping: 265


SQLDATE                                       mega_article
0 2025-01-01  dead tesla cybertruck explodes outside trump h...
1 2025-01-02  cybertruck explosion suspect matthew livelsber...
2 2025-01-03  las vegas soldier’s bomb tesla outside trump h...
3 2025-01-04  lvpd identify driver cybertruck explosion hot ...
4 2025-01-05  tesla sales dropped first annual decline dozen...

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf_vectorizer = TfidfVectorizer(
    max_features= 10000,
    ngram_range=(1, 2),
    min_df=3,
    max_df=0.85,
    sublinear_tf=True

)

X_tfidf = tfidf_vectorizer.fit_transform(mega_df['mega_article'])

print("TF-IDF shape:", X_tfidf.shape)

TF-IDF shape: (265, 10000)


In [ ]:
tfidf_df = pd.DataFrame(
    X_tfidf.toarray(),
    columns=tfidf_vectorizer.get_feature_names_out(),
    index=mega_df['SQLDATE']
)

tfidf_df.head()


aa   aa text     aaron       abc  abc large  abc medium  \
SQLDATE                                                                     
2025-01-01  0.022168  0.000000  0.000000  0.024440   0.014185    0.014185   
2025-01-02  0.006191  0.006642  0.010110  0.012556   0.008751    0.008751   
2025-01-03  0.006979  0.000000  0.007242  0.012447   0.007416    0.007416   
2025-01-04  0.009903  0.010624  0.000000  0.008581   0.000000    0.000000   
2025-01-05  0.000000  0.000000  0.000000  0.000000   0.000000    0.000000   

            abc news  abc small   ability   ablaze  ...        ಕನ     ಕನ ನಡ  \
SQLDATE                                             ...                       
2025-01-01  0.027508   0.014185  0.000000  0.00000  ...  0.000000  0.000000   
2025-01-02  0.013718   0.008751  0.009154  0.00000  ...  0.006642  0.006642   
2025-01-03  0.013048   0.007416  0.006561  0.00605  ...  0.007488  0.007488   
2025-01-04  0.000000   0.000000  0.007511  0.00000  ...  0.000000  0.000000   
2025-01-05  0.000000   0.000000  0.011438  0.00000  ...  0.000000  0.000000   

                  ನಡ    ನಡ മലയ       മലയ    മലയ தம     全球中文版  全球中文版 get  \
SQLDATE                                                                   
2025-01-01  0.000000  0.000000  0.000000  0.000000  0.006601   0.006601   
2025-01-02  0.006642  0.006773  0.006642  0.006773  0.000000   0.000000   
2025-01-03  0.007488  0.007635  0.007488  0.007635  0.004277   0.004277   
2025-01-04  0.000000  0.000000  0.000000  0.000000  0.000000   0.000000   
2025-01-05  0.000000  0.000000  0.000000  0.000000  0.000000   0.000000   

                  日本  日本 polska  
SQLDATE                          
2025-01-01  0.021384   0.022438  
2025-01-02  0.019689   0.020660  
2025-01-03  0.000000   0.000000  
2025-01-04  0.000000   0.000000  
2025-01-05  0.000000   0.000000  

[5 rows x 10000 columns]

In [ ]:
# Save mega articles
mega_df.to_csv('/content/drive/MyDrive/NLPproject/mega_articles.csv', index=False)

# Save TF-IDF features
tfidf_df.to_csv('/content/drive/MyDrive/NLPproject/mega_tfidf.csv')


In [ ]:
!pip install yfinance

import yfinance as yf
import pandas as pd

# Make sure SQLDATE is datetime
mega_df['SQLDATE'] = pd.to_datetime(mega_df['SQLDATE'])

start_date = mega_df['SQLDATE'].min()
end_date   = mega_df['SQLDATE'].max() + pd.Timedelta(days=1)  # yfinance end is exclusive

# Download TSLA daily data
tesla = yf.download('TSLA', start=start_date, end=end_date)

# Use Adjusted Close (or Close)
tesla['return'] = tesla['Close'].pct_change()

up_thr = 0.015  # +1.5%
down_thr = -0.015  # -1.5%

def label_move(r):
    if r > up_thr:
        return 'positive'
    elif r < down_thr:
        return 'negative'
    else:
        return 'neutral'

tesla['label'] = tesla['return'].apply(label_move)

# Keep only the label and turn index into a column
tesla_daily = tesla[['label']].reset_index().rename(columns={'Date': 'SQLDATE'})

tesla_daily.head()


/tmp/ipython-input-3602389099.py:13: FutureWarning: YF.download() has changed argument auto_adjust default to True
  tesla = yf.download('TSLA', start=start_date, end=end_date)
[*********************100%***********************]  1 of 1 completed


Price     SQLDATE     label
Ticker                     
0      2025-01-02   neutral
1      2025-01-03  positive
2      2025-01-06   neutral
3      2025-01-07  negative
4      2025-01-08   neutral

In [ ]:
mega_df = mega_df.reset_index(drop=True)
tesla_daily = tesla_daily.reset_index(drop=False).rename(columns={'Date': 'SQLDATE'})

In [ ]:
print(mega_df.columns)
print(tesla_daily.columns)

Index(['SQLDATE', 'mega_article'], dtype='object')
MultiIndex([(  'index', ''),
            ('SQLDATE', ''),
            (  'label', '')],
           names=['Price', 'Ticker'])


In [ ]:
# --- FLATTEN tesla_daily columns ---
# Turn MultiIndex columns into a simple Index using only the first level
tesla_daily.columns = tesla_daily.columns.get_level_values(0)

print(tesla_daily.columns)
# you should now see: Index(['index', 'SQLDATE', 'label'], dtype='object')

# We don't need the 'index' column
tesla_daily = tesla_daily[['SQLDATE', 'label']].copy()

# Make sure SQLDATE is datetime in both dataframes
mega_df['SQLDATE'] = pd.to_datetime(mega_df['SQLDATE'])
tesla_daily['SQLDATE'] = pd.to_datetime(tesla_daily['SQLDATE'])

# --- NOW MERGE WILL WORK ---
data = pd.merge(mega_df, tesla_daily, on='SQLDATE', how='inner')

print(data.shape)
print(data[['SQLDATE', 'label']].head())


Index(['index', 'SQLDATE', 'label'], dtype='object', name='Price')
(182, 3)
     SQLDATE     label
0 2025-01-02   neutral
1 2025-01-03  positive
2 2025-01-06   neutral
3 2025-01-07  negative
4 2025-01-08   neutral


In [ ]:
# inner join: keep only days where you have both news and price
data = pd.merge(mega_df, tesla_daily, on='SQLDATE', how='inner')

print(data.shape)
data[['SQLDATE', 'label']].head()


(182, 3)


SQLDATE     label
0 2025-01-02   neutral
1 2025-01-03  positive
2 2025-01-06   neutral
3 2025-01-07  negative
4 2025-01-08   neutral

In [ ]:
# Count how many labels of each type exist
label_counts = data['label'].value_counts()
print(label_counts)

label
neutral     62
positive    62
negative    58
Name: count, dtype: int64


In [ ]:
X = tfidf_vectorizer.transform(data['mega_article'])
y = data['label']

In [ ]:
X.shape, y.shape

((182, 10000), (182,))

In [ ]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, confusion_matrix

X_train, X_test, y_train, y_test = train_test_split(
    X, y,
    test_size=0.2,
    stratify=y,
    random_state=42
)

clf = LogisticRegression(max_iter=2000, n_jobs=-1, class_weight='balanced')
clf.fit(X_train, y_train)

y_pred = clf.predict(X_test)

print(classification_report(y_test, y_pred))
print(confusion_matrix(y_test, y_pred))


              precision    recall  f1-score   support

    negative       0.25      0.17      0.20        12
     neutral       0.33      0.31      0.32        13
    positive       0.35      0.50      0.41        12

    accuracy                           0.32        37
   macro avg       0.31      0.32      0.31        37
weighted avg       0.31      0.32      0.31        37

[[2 4 6]
 [4 4 5]
 [2 4 6]]


In [ ]:
# Example: using the first sample
new_text = data['mega_article'].iloc[0]

X_new = tfidf_vectorizer.transform([new_text])
prediction = clf.predict(X_new)[0]

print("Predicted movement:", prediction)


Predicted movement: positive
